In [17]:
from numpy.random import seed
seed(42)
from tensorflow import set_random_seed
set_random_seed(42)
from sklearn.neural_network import MLPRegressor
from keras.models import Sequential
from keras.layers import Dense, SimpleRNN
from keras.optimizers import rmsprop
from keras import backend as ker
from math import sqrt
import numpy as np
import tensorflow as tf
import pandas as pd
import gc


def detrend(insample_data):
    """
    Calculates a & b parameters of LRL

    :param insample_data:
    :return:
    """
    x = np.arange(len(insample_data))
    a, b = np.polyfit(x, insample_data, 1)
    return a, b


def deseasonalize(original_ts, ppy):
    """
    Calculates and returns seasonal indices

    :param original_ts: original data
    :param ppy: periods per year
    :return:
    """
    """
    # === get in-sample data
    original_ts = original_ts[:-out_of_sample]
    """
    if seasonality_test(original_ts, ppy):
        # print("seasonal")
        # ==== get moving averages
        ma_ts = moving_averages(original_ts, ppy)

        # ==== get seasonality indices
        le_ts = original_ts * 100 / ma_ts
        le_ts = np.hstack((le_ts, np.full((ppy - (len(le_ts) % ppy)), np.nan)))
        le_ts = np.reshape(le_ts, (-1, ppy))
        si = np.nanmean(le_ts, 0)
        norm = np.sum(si) / (ppy * 100)
        si = si / norm
    else:
        # print("NOT seasonal")
        si = np.full(ppy, 100)

    return si


def moving_averages(ts_init, window):
    """
    Calculates the moving averages for a given TS

    :param ts_init: the original time series
    :param window: window length
    :return: moving averages ts
    """
    if len(ts_init) % 2 == 0:
        ts_ma = pd.rolling_mean(ts_init, window, center=True)
        ts_ma = pd.rolling_mean(ts_ma, 2, center=True)
        ts_ma = np.roll(ts_ma, -1)
    else:
        ts_ma = pd.rolling_mean(ts_init, window, center=True)

    return ts_ma


def seasonality_test(original_ts, ppy):
    """
    Seasonality test

    :param original_ts: time series
    :param ppy: periods per year
    :return: boolean value: whether the TS is seasonal
    """
    s = acf(original_ts, 1)
    for i in range(2, ppy):
        s = s + (acf(original_ts, i) ** 2)

    limit = 1.645 * (sqrt((1 + 2 * s) / len(original_ts)))

    return (abs(acf(original_ts, ppy))) > limit


def acf(data, k):
    """
    Autocorrelation function

    :param data: time series
    :param k: lag
    :return:
    """
    m = np.mean(data)
    s1 = 0
    for i in range(k, len(data)):
        s1 = s1 + ((data[i] - m) * (data[i - k] - m))

    s2 = 0
    for i in range(0, len(data)):
        s2 = s2 + ((data[i] - m) ** 2)

    return float(s1 / s2)


def split_into_train_test(data, in_num, fh):
    """
    Splits the series into train and test sets. Each step takes multiple points as inputs

    :param data: an individual TS
    :param fh: number of out of sample points
    :param in_num: number of input points for the forecast
    :return:
    """
    train, test = data[:-fh], data[-(fh + in_num):]
    x_train, y_train = train[:-1], np.roll(train, -in_num)[:-in_num]
    x_test, y_test = train[-in_num:], np.roll(test, -in_num)[:-in_num]

    # reshape input to be [samples, time steps, features] (N-NF samples, 1 time step, 1 feature)
    x_train = np.reshape(x_train, (-1, 1))
    x_test = np.reshape(x_test, (-1, 1))
    temp_test = np.roll(x_test, -1)
    temp_train = np.roll(x_train, -1)
    for x in range(1, in_num):
        x_train = np.concatenate((x_train[:-1], temp_train[:-1]), 1)
        x_test = np.concatenate((x_test[:-1], temp_test[:-1]), 1)
        temp_test = np.roll(temp_test, -1)[:-1]
        temp_train = np.roll(temp_train, -1)[:-1]

    return x_train, y_train, x_test, y_test


def rnn_bench(x_train, y_train, x_test, fh, input_size):
    """
    Forecasts using 6 SimpleRNN nodes in the hidden layer and a Dense output layer

    :param x_train: train data
    :param y_train: target values for training
    :param x_test: test data
    :param fh: forecasting horizon
    :param input_size: number of points used as input
    :return:
    """
    # reshape to match expected input
    x_train = np.reshape(x_train, (-1, input_size, 1))
    x_test = np.reshape(x_test, (-1, input_size, 1))

    # create the model
    model = Sequential([
        SimpleRNN(6, input_shape=(input_size, 1), activation='linear',
                  use_bias=False, kernel_initializer='glorot_uniform',
                  recurrent_initializer='orthogonal', bias_initializer='zeros',
                  dropout=0.0, recurrent_dropout=0.0),
        Dense(1, use_bias=True, activation='linear')
    ])
    opt = rmsprop(lr=0.001)
    model.compile(loss='mean_squared_error', optimizer=opt)

    # fit the model to the training data
    model.fit(x_train, y_train, epochs=100, batch_size=1, verbose=0)

    # make predictions
    y_hat_test = []
    last_prediction = model.predict(x_test)[0]
    for i in range(0, fh):
        y_hat_test.append(last_prediction)
        x_test[0] = np.roll(x_test[0], -1)
        x_test[0, (len(x_test[0]) - 1)] = last_prediction
        last_prediction = model.predict(x_test)[0]

    return np.asarray(y_hat_test)


def mlp_bench(x_train, y_train, x_test, fh):
    """
    Forecasts using a simple MLP which 6 nodes in the hidden layer

    :param x_train: train input data
    :param y_train: target values for training
    :param x_test: test data
    :param fh: forecasting horizon
    :return:
    """
    y_hat_test = []

    model = MLPRegressor(hidden_layer_sizes=6, activation='identity', solver='adam',
                         max_iter=100, learning_rate='adaptive', learning_rate_init=0.001,
                         random_state=42)
    model.fit(x_train, y_train)

    last_prediction = model.predict(x_test)[0]
    for i in range(0, fh):
        y_hat_test.append(last_prediction)
        x_test[0] = np.roll(x_test[0], -1)
        x_test[0, (len(x_test[0]) - 1)] = last_prediction
        last_prediction = model.predict(x_test)[0]

    return np.asarray(y_hat_test)


def smape(a, b):
    """
    Calculates sMAPE

    :param a: actual values
    :param b: predicted values
    :return: sMAPE
    """
    a = np.reshape(a, (-1,))
    b = np.reshape(b, (-1,))
    return np.mean(2.0 * np.abs(a - b) / (np.abs(a) + np.abs(b))).item()


def mase(insample, y_test, y_hat_test, freq):
    """
    Calculates MAsE

    :param insample: insample data
    :param y_test: out of sample target values
    :param y_hat_test: predicted values
    :param freq: data frequency
    :return:
    """
    y_hat_naive = []
    for i in range(freq, len(insample)):
        y_hat_naive.append(insample[(i - freq)])

    masep = np.mean(abs(insample[freq:] - y_hat_naive))

    return np.mean(abs(y_test - y_hat_test)) / masep

def remov_nan (dataset):
    '''
    to remove all NaN Values in a 
    Time Serie Dataframe
    '''
    n = dataset.isnull().sum() 
    data = dataset[0:(len(dataset)-n)]
    return data



In [ ]:
def main():
    fh = 6         # forecasting horizon
    freq = 1       # data frequency
    in_size = 3    # number of points used as input for each forecast

    err_MLP_sMAPE = []
    err_MLP_MASE = []
    err_RNN_sMAPE = []
    err_RNN_MASE = []

    # ===== In this example we produce forecasts for 100 randomly generated timeseries =====
    
    data_all = pd.read_csv("../data/Yearly-train.csv", skiprows=0, index_col =0)

    
    #data_all = df_yearly.T
    #data_all = np.array(np.random.random_integers(0, 100, (100, 20)), dtype=np.float32)
    #for i in range(0, 100):
    #    for j in range(0, 20):
    #        data_all[i, j] = j * 10 + data_all[i, j]

    counter = 0
    # ===== Main loop which goes through all timeseries =====
    for j in range(len(data_all)):
        
        ts = data_all.iloc[j]
        ts=remov_nan(ts)

        # remove seasonality
        seasonality_in = deseasonalize(ts, freq)

        for i in range(0, len(ts)):
            ts[i] = ts[i] * 100 / seasonality_in[i % freq]

        # detrending
        a, b = detrend(ts)

        for i in range(0, len(ts)):
            ts[i] = ts[i] - ((a * i) + b)

        x_train, y_train, x_test, y_test = split_into_train_test(ts, in_size, fh)

        # RNN benchmark - Produce forecasts
        y_hat_test_RNN = np.reshape(rnn_bench(x_train, y_train, x_test, fh, in_size), (-1))

        # MLP benchmark - Produce forecasts
        y_hat_test_MLP = mlp_bench(x_train, y_train, x_test, fh)
        for i in range(0, 29):
            y_hat_test_MLP = np.vstack((y_hat_test_MLP, mlp_bench(x_train, y_train, x_test, fh)))
        y_hat_test_MLP = np.median(y_hat_test_MLP, axis=0)

        # add trend
        for i in range(0, len(ts)):
            ts[i] = ts[i] + ((a * i) + b)

        for i in range(0, fh):
            y_hat_test_MLP[i] = y_hat_test_MLP[i] + ((a * (len(ts) + i + 1)) + b)
            y_hat_test_RNN[i] = y_hat_test_RNN[i] + ((a * (len(ts) + i + 1)) + b)

        # add seasonality
        for i in range(0, len(ts)):
            ts[i] = ts[i] * seasonality_in[i % freq] / 100

        for i in range(len(ts), len(ts) + fh):
            y_hat_test_MLP[i - len(ts)] = y_hat_test_MLP[i - len(ts)] * seasonality_in[i % freq] / 100
            y_hat_test_RNN[i - len(ts)] = y_hat_test_RNN[i - len(ts)] * seasonality_in[i % freq] / 100

        # check if negative or extreme
        for i in range(len(y_hat_test_MLP)):
            if y_hat_test_MLP[i] < 0:
                y_hat_test_MLP[i] = 0
            if y_hat_test_RNN[i] < 0:
                y_hat_test_RNN[i] = 0
                
            if y_hat_test_MLP[i] > (1000 * max(ts)):
                y_hat_test_MLP[i] = max(ts)         
            if y_hat_test_RNN[i] > (1000 * max(ts)):
                y_hat_test_RNN[i] = max(ts)

        x_train, y_train, x_test, y_test = split_into_train_test(ts, in_size, fh)

        # Calculate errors
        err_MLP_sMAPE.append(smape(y_test, y_hat_test_MLP))
        err_RNN_sMAPE.append(smape(y_test, y_hat_test_RNN))
        err_MLP_MASE.append(mase(ts[:-fh], y_test, y_hat_test_MLP, freq))
        err_RNN_MASE.append(mase(ts[:-fh], y_test, y_hat_test_RNN, freq))

        # memory handling
        ker.clear_session()
        tf.reset_default_graph()
        gc.collect()

        counter = counter + 1
        print("-------------TS ID: ", counter, "-------------")
        print('MLP_sMAPE',err_MLP_sMAPE[-1],'RNN_sMAPE',err_RNN_sMAPE[-1],'MLP_MASE',err_MLP_MASE[-1],'RNN_MASE',err_RNN_MASE[-1])

    print("\n\n---------FINAL RESULTS---------")
    print("=============sMAPE=============\n")
    print("#### MLP ####\n", np.mean(err_MLP_sMAPE), "\n")
    print("#### RNN ####\n", np.mean(err_RNN_sMAPE), "\n")
    print("==============MASE=============")
    print("#### MLP ####\n", np.mean(err_MLP_MASE), "\n")
    print("#### RNN ####\n", np.mean(err_RNN_MASE), "\n")



main()

/home/jupyter/anaconda3/envs/jupyter/lib/python3.6/site-packages/ipykernel_launcher.py:73: FutureWarning: pd.rolling_mean is deprecated for Series and will be removed in a future version, replace with 
	Series.rolling(window=1,center=True).mean()
/home/jupyter/anaconda3/envs/jupyter/lib/python3.6/site-packages/numpy/core/fromnumeric.py:52: FutureWarning: reshape is deprecated and will raise in a subsequent release. Please use .values.reshape(...) instead
  return getattr(obj, method)(*args, **kwds)


/home/jupyter/anaconda3/envs/jupyter/lib/python3.6/site-packages/ipykernel_launcher.py:73: FutureWarning: pd.rolling_mean is deprecated for Series and will be removed in a future version, replace with 
	Series.rolling(window=1,center=True).mean()
/home/jupyter/anaconda3/envs/jupyter/lib/python3.6/site-packages/numpy/core/fromnumeric.py:52: FutureWarning: reshape is deprecated and will raise in a subsequent release. Please use .values.reshape(...) instead
  return getattr(obj, method)(*args, **kwds)
/home/jupyter/anaconda3/envs/jupyter/lib/python3.6/site-packages/sklearn/neural_network/multilayer_perceptron.py:564: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (100) reached and the optimization hasn't converged yet.
  % self.max_iter, ConvergenceWarning)


-------------TS ID:  1 -------------


/home/jupyter/anaconda3/envs/jupyter/lib/python3.6/site-packages/ipykernel_launcher.py:73: FutureWarning: pd.rolling_mean is deprecated for Series and will be removed in a future version, replace with 
	Series.rolling(window=1,center=True).mean()


-------------TS ID:  2 -------------
-------------TS ID:  3 -------------
-------------TS ID:  4 -------------
-------------TS ID:  5 -------------
-------------TS ID:  6 -------------
-------------TS ID:  7 -------------
-------------TS ID:  8 -------------
-------------TS ID:  9 -------------


KeyboardInterrupt: 

In [3]:
data_all = np.array(np.random.random_integers(0, 100, (100, 20)), dtype=np.float32)
print("richtig",data_all.shape)
data_all

richtig (100, 20)


/home/jupyter/anaconda3/envs/jupyter/lib/python3.6/site-packages/ipykernel_launcher.py:1: DeprecationWarning: This function is deprecated. Please call randint(0, 100 + 1) instead
  """Entry point for launching an IPython kernel.


array([[ 71.,  83.,  37., ...,  55.,  38.,  69.],
       [ 82.,  57.,  22., ...,  14.,   1.,  60.],
       [ 58.,  16.,  10., ...,  47.,  94.,  52.],
       ...,
       [ 85.,  39.,  28., ...,  11., 100.,  87.],
       [ 48.,  96.,  80., ...,  98.,   9.,   7.],
       [ 17.,  16.,  68., ...,  35.,  54.,  36.]], dtype=float32)

In [23]:
data_all = pd.read_csv("../data/Yearly-train.csv", skiprows=0, index_col =0)
for j in range(len(data_all)): 
    ts = data_all.iloc[j]
    ts=remov_nan(ts)
    print(j,ts.as_matrix())

0 [5172.1 5133.5 5186.9 5084.6 5182.  5414.3 5576.2 5752.9 5955.2 6087.8
 6238.9 6317.2 6262.7 6361.  6427.4 6654.9 6835.4 6925.5 7073.5 7144.
 7230.6 7349.6 7339.2 7250.8 7294.6 7393.9 7560.9 7651.4 7587.3 7530.5
 7261.1]
1 [2070. 2104. 2394. 1651. 1492. 1348. 1198. 1192. 1105. 1008.  994. 1420.
 1582. 1286. 1133. 1322. 1157. 1244. 1843. 1794. 1426. 1170. 1021.  997.
 1062. 1013.  944.  861. 1002. 1302. 1603.]
2 [2760. 2980. 3200. 3450. 3670. 3850. 4000. 4160. 4290. 4530. 4720. 4890.
 5070. 5220. 5420. 5660. 5820. 5940. 6070. 6200. 6520. 6690. 6930. 7060.
 7230. 7430. 7480. 7730. 7900. 8220. 8380.]
3 [3380. 3670. 3960. 4190. 4440. 4700. 4890. 5060. 5200. 5490. 5690. 5910.
 6120. 6340. 6530. 6710. 6850. 6980. 7130. 7320. 7630. 7710. 7990. 8070.
 8340. 8570. 8530. 8970. 9090. 9440. 9670.]
4 [1980. 2030. 2220. 2530. 2610. 2720. 2970. 2980. 3100. 3230. 3340. 3430.
 3810. 3780. 3930. 3840. 3890. 3840. 3930. 4050. 4040. 4630. 4880. 5020.
 5160. 5600. 5690. 5830. 6050. 6440. 6840.]
5 [1988.6

326 [9127.16787  8018.446312 5815.546098 3603.780534 3556.344137 3952.414122
 4935.142165 5184.403281 5329.875611 4760.454623 5362.50012  5377.642724
 5585.746313 5778.120026 6036.545344]
327 [ 795.4169116  843.6073197  908.3020271  976.3686132 1049.743518
 1130.692595  1221.066907  1321.137995  1420.916635  1508.063427
 1592.481499  1686.7333    1745.174285  1784.829304  1869.731998
 1864.409894  1943.686046  2135.692326  2252.140925  2315.756514
 2454.063202  2471.142366  2727.463227  2813.997094  2865.49582
 2913.684565  2849.617947  2790.082718  2614.89499   2498.245549
 2545.036403  2569.534618  2751.388405  3108.355419  3842.73169  ]
328 [3687.126699 3742.761716 3523.201442 3499.195955 3215.098544 3272.575248
 3177.296538 3215.638493 3146.695277 3138.631577 3003.830937 3119.551419
 3121.844311 3326.09998  3232.325963 3165.976172 2937.472976 3117.625446
 2616.691595 2699.255614 2610.996747 2514.951911 2801.370883 3149.95245
 3110.063569 3509.40869  4192.042592 4319.707119 4420.190

669 [1450.4207 1640.7214 1780.8222 1856.465  1972.8262 2098.5579 2251.3115
 2379.8564 2481.7263 2493.8748 2535.2237 2699.3487 3053.4283 3389.4971
 4013.2721 3881.8707 3597.7055 3205.3099]
670 [1148.67 1126.72 1143.71 1153.44 1220.51 1250.19 1274.18 1332.19 1398.3
 1403.67 1440.22 1420.1  1498.01 1500.37 1561.24 1600.68 1656.4  1666.18]
671 [ 3782.3  5109.2  5792.3  6538.7  6349.6  6996.6  7015.7  6794.1  6419.3
  7993.9  9273.8  9061.  11737.6 11468.2  7673.1  7303.5  7009.   7285.1]
672 [ 841.35 1460.7  2037.31 2078.37 2080.92 2020.56 1701.13 2176.06 2354.88
 2381.95 2684.28 2222.07 2799.91 2851.61 2811.17 2899.31 2966.48 2834.06]
673 [ 6776.8  5312.7  6842.9  4729.6  6554.7  6757.   6175.5  5241.4  7527.1
  6049.9  5264.   3060.3  5811.9 12412.5 14808.4 10084.7 10529.4  7859.7]
674 [ 402.8  376.1  792.2  641.   620.2  578.1  706.   769.1  945.2 1036.8
 1006.8 1181.8 1842.6 2431.6 5657.4 4832.4 3831.6 2377.3]
675 [5070. 5100. 5090. 5070. 5320. 5470. 5550. 5520. 5380. 5280. 5230. 5020.

1047 [1270. 1660. 1890. 2020. 2220. 2210. 3500. 2510. 1930. 1920. 1920. 2110.
 2220. 2950. 3000. 3480. 4540. 4640. 2550. 1450.]
1048 [4546.7 4620.  4670.  4720.  4820.  4950.  5010.  5130.  5240.  5380.
 5602.5 5672.1 5717.5 5714.9 5700.7 5686.2 5708.7 5746.8 5778.8 5866.3
 5954.6 6073.1 6145.5 6323.7 6449.  6569.  6657.2 6731.5 6785.8 6834.5
 6859.7 6887.4 6933.5 7017.7 7074.2 7169.1 7286.7 7375.2 7438.6 7476.5]
1049 [2652.36 2679.   2626.   2661.   2659.   2735.   2792.   2870.   3034.
 3234.   3377.2  3511.69 3565.63 3599.21 3681.05 3770.91 3889.67 4048.71
 4251.9  4463.25 4710.8  4844.5  5002.83 5139.59 5239.11 5338.7  5456.12
 5681.84 5873.5  5979.31 6090.93 6220.49 6308.12 6344.19 6418.95 6527.33
 6679.37 6806.1  6904.82 7012.19]
1050 [2874.87 2969.   2996.   3035.   3094.   3112.   3160.   3212.   3292.
 3349.   3418.35 3466.75 3474.4  3487.01 3533.58 3557.34 3547.78 3542.7
 3540.92 3562.7  3630.29 3727.7  3830.2  3927.88 3985.44 4046.52 4081.97
 4102.   4135.1  4154.26 4189.3  

1365 [ 480.  550.  590.  640.  670.  680.  700.  700.  750.  830.  890.  950.
  990. 1020. 1060. 1160. 1310. 1480. 1580. 1780. 1850.]
1366 [ 713.  761.  804.  849.  880.  912.  938.  953.  968.  982. 1010. 1041.
 1084. 1140. 1213. 1291. 1369. 1449. 1532. 1647. 1777.]
1367 [1150. 1190. 1250. 1300. 1350. 1410. 1430. 1450. 1440. 1440. 1450. 1490.
 1520. 1550. 1570. 1600. 1630. 1630. 1650. 1690. 1740.]
1368 [1680. 1920. 2000. 2100. 2260. 2400. 2570. 2710. 3030. 3390. 3660. 3980.
 4220. 4530. 4970. 5650. 6290. 7170. 7900. 8640. 8770.]
1369 [ 304.  257.  272.  343.  367.  384.  371.  396.  593.  535.  449.  465.
  551.  681.  763.  815.  963. 1211. 1483. 1786. 1785.]
1370 [ 540.  370.  540.  530.  450.  470. 1160.  770.  810.  670.  570.  940.
 1100. 1280. 1950. 2600. 3170. 2930. 6330. 1730. 1200.]
1371 [ 4370.  4060.  4800.  5330.  6050.  5810.  5060.  4610.  4250.  3910.
  4770.  4400.  5820.  6230.  9320. 10500. 11410. 11870. 13280. 13820.
 14430.]
1372 [ 866.  604.  660.  639.  804.  864

...

21399 [ 9200. 10300.  9900.  9200.  8800.  8300.  7500.  6800.  6200.  5400.
  5400.  4800.  4300.  4500.  4400.  4000.  3300.  3200.  5700.  5600.
  5500.  5100.]
21400 [ 5718.7   5091.22  4638.58  6066.24  6162.12  7007.77  6469.8   7084.93
 10499.43  8253.32  7445.57  7298.49  9044.79 11907.17  6034.5 ]
21401 [ 2249.83  2121.47  2237.4   2429.99  3338.44  4627.    5129.79  5060.8
 10278.57  6143.83  6466.48  7016.36  7714.65  6953.98  7307.63 11913.01
 10340.74  9939.76  8296.15  5367.07  5341.24  7936.33]
21402 [ 353.679  353.393  361.653  423.025  550.587  754.368  796.487  924.805
 1441.485  961.118 1097.683 1771.433 2326.489 1570.078 1670.643 1884.304
 1772.342 1809.477 2046.663 1326.403 1059.528  972.853]
21403 [2617.94265 2941.21243 3339.90894 3637.33247 3823.85389 3956.98176
 4059.07037 4258.02807 4400.55528 4573.62857 4727.57458 4845.79002
 4980.27339 5054.7081  5214.27263 5401.87392 5630.17882 5873.60187
 6186.70065 6432.90639 6651.21756 6891.93374]
21404 [1234.8362 1722.03

21771 [7130. 6990. 6920. 6770. 6830. 6960. 7070. 6840. 6630. 6820. 7010. 7140.
 7280. 7270. 7210. 7390. 7520. 7660. 7390. 7340. 7320. 7390. 7400. 7370.
 7400. 7240.]
21772 [7230. 6960. 7040. 7250. 7370. 7220. 6940. 7180. 7040. 6970. 6920. 7110.
 7300. 7370. 7510. 7490. 7520. 7450. 7490. 7340. 7400. 7880. 7620. 7400.
 7540. 7550.]
21773 [6710. 6550. 6480. 6640. 6790. 6700. 6500. 6680. 6660. 6540. 6510. 6600.
 6500. 6680. 6960. 7020. 6920. 6840. 6950. 7440. 7330. 7400. 7420. 7380.
 7500. 7600.]
21774 [5110. 5030. 5130. 5200. 5070. 5230. 5330. 5260. 5330. 5280. 5250. 5270.
 5270. 5260. 5280. 5280. 5340. 5390. 5480. 5430. 5480. 5590. 5570. 5590.
 5500. 5440.]
21775 [7010. 6990. 6920. 6890. 6770. 6710. 6720. 6540. 6370. 6270. 6330. 6730.
 6820. 6810. 6800. 7010. 7070. 7100. 6940. 6870. 7000. 6850. 6830. 6600.
 6660. 6570.]
21776 [6090. 6140. 6220. 6040. 6200. 6120. 5850. 5820. 5680. 5760. 5650. 5790.
 5660. 5870. 5980. 6060. 6150. 6010. 5940. 5990. 6150. 6310. 6460. 6490.
 6450. 6290.]
2177

22167 [5470.3 5696.5 5863.2 6028.2 6153.6 6194.6 6430.  6859.5 7235.3 7536.5
 7965.7 8471.6 8821.4 9123.4 8888.4]
22168 [8651.4 8359.1 8029.3 8324.2 8005.8 7920.9 8097.8 8480.2 9007.6 9192.7
 9125.4 9884.8 9838.6 9308.8 8812.8]
22169 [6147.7 6656.  6849.7 7013.2 7128.8 6977.  7532.6 7973.3 8750.  8686.9
 8937.9 9399.  9288.5 9573.1 8847. ]
22170 [ 892.82  970.06 1013.46 1161.54 1126.82 1030.62 1046.98 1141.17 1085.88
 1117.9  1135.84 1219.31 1268.72 1251.07 1074.35]
22171 [ 4440.3  5952.8  5453.5  7107.   7337.   7898.8  7862.3  8061.   8563.7
  8256.1  9280.2  8807.8 10069.9  8579.7  8081.6]
22172 [ 6940.7  7263.4  7418.1  7169.5  7032.   7169.3  6989.2  7537.6  7839.1
  8443.   8467.2  9659.1  9662.6 10237.1 10039.6]
22173 [3777.3 4137.9 4482.8 4725.5 5099.  4889.3 5372.4 5720.2 6150.6 6786.5
 7056.9 7156.9 7756.6 8303.3 8519.3]
22174 [3121.5 3221.3 3432.2 3656.1 3920.8 3832.5 3919.7 4030.8 4373.5 4682.
 7149.2 8274.7 8988.3 9476.6 8755.3]
22175 [ 2120.  2190.  2290.  2480.  2500.  2

22499 [ 8360.  8870.  8770.  9200.  9650.  9980. 10340. 10310. 10160. 10120.
 10190. 10200. 10920. 10780. 10670. 10400. 10130.  9880.  9770.  9450.
  9440.  9380.  9540.  9650.  9710.  9540.]
22500 [ 931.9  997.8 1067.4 1128.2 1229.5 1413.9 1681.5 1950.5 2222.7 2381.3
 2453.5 2573.8 2692.  2845.7 2924.5 3065.3 3165.5 3306.  3294.6 3447.9
 3766.  4119.9 4448.  4872.3 5216.7 5558.7]
22501 [ 558.27  572.03  586.74  608.87  627.35  643.71  647.78  645.17  647.34
  655.32  669.69  678.23 1494.27 1509.66 1554.71 1576.69 1610.82 1625.35
 1682.21 1706.78 1724.08 1731.58 1734.15 1735.51 1723.25 1753.92]
22502 [ 467.49  507.88  554.65  612.32  669.86  755.21  827.76  868.51  900.95
  937.86  990.6  1047.02 1097.57 1135.09 1193.62 1238.46 1293.2  1328.89
 1378.97 1420.68 1476.03 1522.5  1562.54 1605.83 1609.22 1620.96]
22503 [1493.9 1541.9 1556.7 1536.1 1554.2 1534.9 1606.  1620.3 1660.8 1662.5
 1656.  1701.3 1690.9 1721.2 1657.2 1697.4 1709.7 1717.6 1744.1 1886.1
 1892.7 1893.  1772.4 1852.1 178

22828 [3600. 3700. 2900. 2700. 2400. 3700. 2800. 3000. 3800. 3300. 3800. 4400.
 4500.]
22829 [5020. 4950. 4960. 4850. 4240. 4560. 4690. 4680. 5100. 4630. 4990. 4490.
 5210.]
22830 [1191. 1165. 1145. 1096. 1029. 1053. 1124. 1047. 1199.  950. 1016.  853.
  963.]
22831 [2333. 2482. 2898. 3696. 4382. 5521. 5529. 5654. 7232. 7826. 8549. 8654.
 9951.]
22832 [1490. 1360. 1330. 1550. 1820. 2190. 2780. 3210. 4370. 4680. 4940. 5540.
 5870.]
22833 [1540. 1530. 1590. 1630. 1210. 1330. 1460. 1370. 1290. 1340. 1720. 1480.
 1490.]
22834 [5530. 5450. 6220. 6650. 5670. 7450. 7820. 7090. 8070. 8220. 8600. 6640.
 8390.]
22835 [10300. 11900. 13800. 13200.  8800.  9900. 10500. 10500. 10300. 10500.
 10700.  9200.  8400.]
22836 [ 6430.  7880.  9510.  8370.  8720.  9350.  9900. 11740. 11160.  7320.
  6850.  4220.  5250.]
22837 [1837. 1889. 2239. 1762. 1417. 1573. 1931. 2552. 2733. 1361. 1248.  951.
  953.]
22838 [ 149.  118.  194.  261.  411.  644.  434.  666.  694. 1136. 1208. 1249.
 1494. 1899. 1484. 1802. 